In [1]:
#data imports
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
#model imports
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from torch.utils.data import Dataset


In [2]:
#import rmnp weather csv
weather = pd.read_csv('/Users/ethancrouse/Desktop/rmnp_weather_10yrs.csv')
weather

Date  Bear Lake (322) Precipitation Accumulation (in)  \
0       2013-12-07 0:00                                              6.5   
1       2013-12-07 1:00                                              6.5   
2       2013-12-07 2:00                                              6.5   
3       2013-12-07 3:00                                              6.5   
4       2013-12-07 4:00                                              6.6   
...                 ...                                              ...   
87162  2023-12-07 19:00                                              5.6   
87163  2023-12-07 20:00                                              5.6   
87164  2023-12-07 21:00                                              5.6   
87165  2023-12-07 22:00                                              5.5   
87166  2023-12-07 23:00                                              5.5   

       Bear Lake (322) Air Temperature Observed (degF)  \
0                                                  6.3   
1                                                  7.7   
2                                                  9.0   
3                                                  8.4   
4                                                  8.6   
...                                                ...   
87162                                             27.5   
87163                                             26.8   
87164                                             24.8   
87165                                             24.6   
87166                                             23.7   

       Bear Lake (322) Wind Speed Average (mph)  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   
...                                         ...   
87162                                       1.5   
87163                                       2.2   
87164                                       1.9   
87165                                       0.9   
87166                                       0.9   

       Bear Lake (322) Snow Water Equivalent (in)  \
0                                             5.3   
1                                             5.3   
2                                             5.4   
3                                             5.4   
4                                             5.4   
...                                           ...   
87162                                         4.0   
87163                                         4.0   
87164                                         4.0   
87165                                         4.0   
87166                                         4.0   

       Bear Lake (322) Snow Depth (in)  Bear Lake (322) Snow Density (pct)  \
0                                 27.0                                 NaN   
1                                 27.0                                 NaN   
2                                 27.0                                 NaN   
3                                 27.0                                 NaN   
4                                 27.0                                 NaN   
...                                ...                                 ...   
87162                             17.0                                 NaN   
87163                             17.0                                 NaN   
87164                             17.0                                 NaN   
87165                             17.0                                 NaN   
87166                             17.0                                 NaN   

       Bear Lake (322) Snow Water Equivalent Maximum (in)  
0                                                    NaN   
1                                                    NaN   
2                                         

In [3]:
#print info
weather.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 87167 entries, 0 to 87166
Data columns (total 8 columns):
 #   Column                                              Non-Null Count  Dtype  
---  ------                                              --------------  -----  
 0   Date                                                87167 non-null  object 
 1   Bear Lake (322) Precipitation Accumulation (in)     86905 non-null  float64
 2   Bear Lake (322) Air Temperature Observed (degF)     87094 non-null  float64
 3   Bear Lake (322) Wind Speed Average (mph)            43330 non-null  float64
 4   Bear Lake (322) Snow Water Equivalent (in)          80501 non-null  float64
 5   Bear Lake (322) Snow Depth (in)                     78276 non-null  float64
 6   Bear Lake (322) Snow Density (pct)                  0 non-null      float64
 7   Bear Lake (322) Snow Water Equivalent Maximum (in)  0 non-null      float64
dtypes: float64(7), object(1)
memory usage: 5.3+ MB


In [4]:
#remove columns with only null entries
weather.drop(['Bear Lake (322) Snow Water Equivalent Maximum (in)',
                'Bear Lake (322) Snow Density (pct)'],axis=1,inplace=True)
weather.head()

Date  Bear Lake (322) Precipitation Accumulation (in)  \
0  2013-12-07 0:00                                              6.5   
1  2013-12-07 1:00                                              6.5   
2  2013-12-07 2:00                                              6.5   
3  2013-12-07 3:00                                              6.5   
4  2013-12-07 4:00                                              6.6   

   Bear Lake (322) Air Temperature Observed (degF)  \
0                                              6.3   
1                                              7.7   
2                                              9.0   
3                                              8.4   
4                                              8.6   

   Bear Lake (322) Wind Speed Average (mph)  \
0                                       NaN   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4                                       NaN   

   Bear Lake (322) Snow Water Equivalent (in)  Bear Lake (322) Snow Depth (in)  
0                                         5.3                             27.0  
1                                         5.3                             27.0  
2                                         5.4                             27.0  
3                                         5.4                             27.0  
4                                         5.4                             27.0

In [5]:
#pulling out temps for timeseries prediction
temps = weather.iloc[:,4]

'''
#use 2/3 of dataset to shave down computational cost:
two_thirds = int(.67 * len(temps))
temps = temps[:two_thirds]
'''

#remove nan values
temps = temps.dropna()

#normalize data for stable model training
temps_array = temps.to_numpy()
def min_max_norm(x):
    return ((x-min(x)) / (max(x) - min(x)))

#data is pretty fine-course, collected hourly. sliding window mean will simplify the data 
def sliding_window_mean(x,n):
    return np.convolve(x, np.ones(n)/n, mode='valid')

#normalize and window-average
smooth_out = 250
timeseries = sliding_window_mean(temps_array,smooth_out)
timeseries = min_max_norm(timeseries)

In [6]:
#plotting
plt.style.use('dark_background')
x = np.arange(0,timeseries.size)
plt.figure(figsize=(10,5),dpi=1200)
plt.title('Observed Snow Depth in Bear Lake, RMNP --- 2013-2023')
plt.xlabel(f'Timepoint (Hourly, 10 yrs) - Sliding-Window Averaged({smooth_out} hrs)')
plt.ylabel('Depth (inches) - Normalized')

plt.scatter(x,timeseries,s=.1,cmap='magma',c=timeseries)
plt.show()

In [7]:
#track data dimensionality
print(type(timeseries),timeseries.shape)

<class 'numpy.ndarray'> (80252,)


In [8]:
#The length of the sequence that will be fed as an input to the model
sequence_length = 100
#The number of timesteps we will attempt to predict with the model
label_length = 100
#train/test split
train_split = .80
stop_index = int(train_split * len(timeseries))
train_samples = timeseries[:stop_index]
test_samples = timeseries[stop_index:]

#produce sequences and their labels of train/test datasets
def produce_sequences(series,label_length):
    data = []
    labels = []
    for i in range(0,len(series)-sequence_length):
        data.append(series[i:i+sequence_length])
        labels.append(series[(i+sequence_length):((i+sequence_length)+label_length)])
    return data,labels

train_data,train_labels = produce_sequences(train_samples,label_length)
test_data,test_labels = produce_sequences(test_samples,label_length)

print("Data types in test_labels:", set(type(x) for y in test_labels for x in y))
print("Data types in train_labels:", set(type(x) for y in train_labels for x in y))

#remove sequences with less than the window size:
train_data = train_data[:-1000]
train_labels = train_labels[:-1000]
test_data = test_data[:-1000]
test_labels = test_labels[:-1000]

'''
#train/test split - logical error explained below
#using this code randomly samples data for test/split, 
#resulting in data leakage because of temporal relationships between nearby train/test samples

for i in range(0,len(timeseries)-sequence_length):
    p = np.random.uniform(0, 1)
    if p <= train_split:
        train_data.append(timeseries[i:i+sequence_length])
        train_labels.append(timeseries[i+sequence_length])
    else:
        test_data.append(timeseries[i:i+sequence_length])
        test_labels.append(timeseries[i+sequence_length])
'''

Data types in test_labels: {<class 'numpy.float64'>}
Data types in train_labels: {<class 'numpy.float64'>}


'\n#train/test split - logical error explained below\n#using this code randomly samples data for test/split, \n#resulting in data leakage because of temporal relationships between nearby train/test samples\n\nfor i in range(0,len(timeseries)-sequence_length):\n    p = np.random.uniform(0, 1)\n    if p <= train_split:\n        train_data.append(timeseries[i:i+sequence_length])\n        train_labels.append(timeseries[i+sequence_length])\n    else:\n        test_data.append(timeseries[i:i+sequence_length])\n        test_labels.append(timeseries[i+sequence_length])\n'

In [9]:
#convert to torch.tensors for model input
train_X = torch.FloatTensor((train_data)).unsqueeze(-1)
train_Y = torch.FloatTensor((train_labels)).unsqueeze(-1)

test_X = torch.FloatTensor((test_data)).unsqueeze(-1)
test_Y = torch.FloatTensor((test_labels)).unsqueeze(-1)

#track data dimensionality
print(f"After data split: \nTraining data shape: x: {train_X.shape} y: {train_Y.shape}")
print(f"Testing data shape: x: {test_X.shape} y: {test_Y.shape}\n")

<ipython-input-9-77bcabbce856>:2: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at  /private/var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_croot-udngs7fm/pytorch_1648016055234/work/torch/csrc/utils/tensor_new.cpp:201.)
  train_X = torch.FloatTensor((train_data)).unsqueeze(-1)


After data split: 
Training data shape: x: torch.Size([63101, 100, 1]) y: torch.Size([63101, 100, 1])
Testing data shape: x: torch.Size([14951, 100, 1]) y: torch.Size([14951, 100, 1])



In [10]:
#create dataset class --- integrates with DataLoader class
class TimeSeriesDataset(Dataset):
    def __init__(self, X, Y):
        self.X = X
        self.Y = Y
        
    #return length
    def __len__(self):
        return len(self.X)
    
    #return item
    def __getitem__(self,i):
        return {'data': self.X[i], 'target': self.Y[i]}

#initialize set 
train_set = TimeSeriesDataset(train_X,train_Y)
test_set = TimeSeriesDataset(test_X,test_Y)

#initialize dataloader - faster dataset loading onto CPU
#shuffle = True for non-stately, False for stately
batch_size = 16
train_loader = DataLoader(train_set, 
                          batch_size = batch_size, 
                          shuffle = True)

test_loader = DataLoader(test_set, 
                          batch_size = batch_size, 
                          shuffle = False)

#track dimensionality
for index,batch in enumerate(train_loader):
    x_batch, y_batch = batch['data'],batch['target']
    print(f'Batched data size: {x_batch.shape}\nBatched label size: {y_batch.shape}')
    break

Batched data size: torch.Size([16, 100, 1])
Batched label size: torch.Size([16, 100, 1])


In [11]:
device = 'cuda:0' if torch.cuda.is_available() else 'cpu'

#Define LSTM unit
class non_stateful_LSTMunit(nn.Module):
    def __init__(self,input_size,hidden_size,n_recurrent_modules,n_prediction_steps):
        super(non_stateful_LSTMunit, self).__init__()
        
        #number of festures per timestep
        self.input_size = input_size
        #number of features in hidden state and cell state
        self.hidden_size = hidden_size
        #number of recurrent LSTM modules
        self.n_recurrent_modules = n_recurrent_modules
        #number of prediction steps
        self.n_prediction_steps = n_prediction_steps
        
        #lstm module
        self.lstm = nn.LSTM(input_size,
                            hidden_size,
                            n_recurrent_modules,
                            batch_first=True,
                            dropout= .2)
        
        #output layer - predict same number of features as input_size
        self.fc = nn.Linear(hidden_size,n_prediction_steps)

    def forward(self, x,last_hidden_state = None):
        #pull batch size from input 
        batch_size = x.size(0)
        
        if x.dim() != 3:
            x = x.unsqueeze(2)
    
        #non-stately LSTM - reset states between batches
        c0 = torch.zeros(self.n_recurrent_modules, batch_size, self.hidden_size).to(x.device)
        h0 = torch.zeros(self.n_recurrent_modules, batch_size, self.hidden_size).to(x.device)
    
        '''
        #stateful --- keep track of hidden states between sequences, enables long term memory 
        if last_hidden_state is None:
            batch_size = x.size(0)
            c0 = torch.zeros(self.n_recurrent_modules, batch_size, self.hidden_size).to(x.device)
            h0 = torch.zeros(self.n_recurrent_modules, batch_size, self.hidden_size).to(x.device)
        else:
            c0, h0 = last_hidden_state
        '''

        #pass through lstm -- output shape is (batch_size, sequence_length, hidden_size)
        out, (cn,hn) = self.lstm(x,(c0,h0))

        # Update hidden states for the next prediction
        last_hidden_state = (cn.detach(), hn.detach())

        #for predicting timeseries data we select the hidden state from the last timestep for each sequence in the batch to pass through fc layer
        out = self.fc(out[:,-1,:])

        return out

In [12]:
#instantiate model
model = non_stateful_LSTMunit(input_size = 1,
                hidden_size = 64,
                n_recurrent_modules = 2,
                n_prediction_steps = label_length)
model

non_stateful_LSTMunit(
  (lstm): LSTM(1, 64, num_layers=2, batch_first=True, dropout=0.2)
  (fc): Linear(in_features=64, out_features=100, bias=True)
)

In [13]:
#instantiate optimizer, loss, and containers
learning_rate = 0.001
training_epochs = 5
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
loss_function = nn.MSELoss()

In [14]:
#epoch of training
def training_step():
    training_losses = []
    model.train(True)
    for _, batch in enumerate(train_loader):
        #compute output and loss
        data,target = batch['data'].to(device),batch['target'].to(device)
        output = model.forward(data)
        loss = loss_function(output,target.squeeze())
        #backpropagate error
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        #return training loss per batch
        training_losses.append(loss.detach())
    
    return training_losses

#epoch of validation
def validation_step():
    validation_losses = []
    model.train(False)
    for _, batch in enumerate(test_loader):
        data, target = batch['data'].to(device), batch['target'].to(device)
        #break gradient graph
        with torch.no_grad():
            output = model.forward(data)
            #return validation loss per batch
            validation_loss = loss_function(output,target.squeeze())
            validation_losses.append(validation_loss)
    
    return validation_losses

In [15]:
#training loop
training_losses = []
validation_losses = []
for epoch in range(training_epochs):
    training_losses.append(training_step())
    validation_losses.append(validation_step())
    print(f"Epoch: {epoch+1}, training losses average: {np.mean(np.array(training_losses).flatten())}\n"
          f"          validation losses average: {np.mean(np.array(validation_losses).flatten())}\n")

Epoch: 1, training losses average: 0.0019065942615270615
          validation losses average: 0.0004866486706305295

Epoch: 2, training losses average: 0.001253322814591229
          validation losses average: 0.00047024161904118955

Epoch: 3, training losses average: 0.0010194614296779037
          validation losses average: 0.0004486266407184303

Epoch: 4, training losses average: 0.0008831679588183761
          validation losses average: 0.00045383378164842725

Epoch: 5, training losses average: 0.0008032032055780292
          validation losses average: 0.00042284070514142513



In [16]:
#plotting training losses
plt.style.use('dark_background')
x = np.arange(0,len(np.array(training_losses).flatten()))
plt.figure(figsize=(10,5),dpi=1200)
plt.title('Loss over Training Iterations')
plt.xlabel(f'Iteration')
plt.ylabel('Loss (MSE)')
plt.scatter(x,np.array(training_losses).flatten(),s=.2,cmap='magma')
plt.show()

#plotting validation losses
plt.style.use('dark_background')
x = np.arange(0,len(np.array(validation_losses).flatten()))
plt.figure(figsize=(10,5),dpi=1200)
plt.title('Validation Loss over Training Iterations')
plt.xlabel(f'Iteration')
plt.ylabel('Loss (MSE)')
plt.scatter(x,np.array(validation_losses).flatten(),s=.2,c='darkorchid')
plt.show()

In [17]:
#test out the model on training data
with torch.no_grad():
    training_predicted = model.forward(train_X[:].to(device)).numpy()

#plot training data vs. prediction 
plt.figure(figsize=(10,5),dpi=1200)
plt.style.use('dark_background')
#training data
x = np.arange(0,len(np.array(train_Y).flatten()))
plt.scatter(x,train_Y,s=4,c='r')
#prediction
x = np.arange(0,len(np.array(training_predicted).flatten()))
plt.title('LSTM prediction on Training Data')
plt.xlabel(f'Timepoint (Window Average, {smooth_out}hrs)')
plt.ylabel('Normalized Snow Depth')
plt.scatter(x,np.array(training_predicted).flatten(),s=.2,c='b',marker='+')

plt.show()


#test out the model on testing data
with torch.no_grad():
    test_predicted = model.forward(test_X[:].to(device)).numpy()

#Validate model on the validation set:
#plot training data vs. prediction 
plt.figure(figsize=(10,5),dpi=1200)
plt.style.use('dark_background')
#test data
x = np.arange(0,len(np.array(test_Y).flatten()))
plt.scatter(x,test_Y,s=4,c='r')
#prediction
x = np.arange(0,len(np.array(test_predicted).flatten()))
plt.title('LSTM prediction on Validation Data')
plt.xlabel(f'Timepoint (Window Average, {smooth_out}hrs)')
plt.ylabel('Normalized Snow Depth')
plt.scatter(x,np.array(test_predicted).flatten(),s=.2,c='b',marker='+')

plt.show()

In [18]:
#running prediction into future
def autoregressive_prediction(start_sequence, n_iterations, sequence_length):
    predictions = []
    
    #pull last sequence from x
    current_sequence = (start_sequence[-1,:].unsqueeze(0)).clone()
    
    #make a new prediction, new prediction becomes next input
    with torch.no_grad():
        for n in range(n_iterations):
            new_prediction = model.forward(current_sequence.to(device))
            current_sequence = new_prediction
            predictions.append(new_prediction.numpy())
    
    return predictions
#combine predictions with past test prredictions for visualization
predictions = autoregressive_prediction(test_X,1000,sequence_length)
predictions = np.array(predictions).flatten()
predictions = np.concatenate((test_predicted.squeeze().flatten(),predictions))
            
'''
#autoregressive prediction - predicting one sample, and iteratively including predictions 
#into new input sequences
def autoregressive_prediction(start_sequence,n_iterations,sequence_length):
    #make predictions on sequences of predicted data
    predictions = []
    with torch.no_grad():
        current_sequence = torch.tensor([])
        predicted_start = model.forward(start_sequence.to(device))
        current_sequence = torch.cat((current_sequence,predicted_start[-sequence_length:]))
        #iteratively add predictions to sequence
        for n in range(n_iterations):
            #model forward method accepts:[batch, sequence length, features]
            print(current_sequence.shape)
            new_prediction = model.forward(current_sequence[:,0].to(device).unsqueeze(0))
            predictions.append(new_prediction.item())
            #add prediction to sequence window
            current_sequence = torch.cat((current_sequence[1:],new_prediction))
    #return list of predictions
    return predictions, predicted_start.numpy()

predictions, predicted_start = autoregressive_prediction(test_X,400,20)
predictions = np.concatenate((predicted_start.squeeze(),predictions))
'''

'\n#autoregressive prediction - predicting one sample, and iteratively including predictions \n#into new input sequences\ndef autoregressive_prediction(start_sequence,n_iterations,sequence_length):\n    #make predictions on sequences of predicted data\n    predictions = []\n    with torch.no_grad():\n        current_sequence = torch.tensor([])\n        predicted_start = model.forward(start_sequence.to(device))\n        current_sequence = torch.cat((current_sequence,predicted_start[-sequence_length:]))\n        #iteratively add predictions to sequence\n        for n in range(n_iterations):\n            #model forward method accepts:[batch, sequence length, features]\n            print(current_sequence.shape)\n            new_prediction = model.forward(current_sequence[:,0].to(device).unsqueeze(0))\n            predictions.append(new_prediction.item())\n            #add prediction to sequence window\n            current_sequence = torch.cat((current_sequence[1:],new_prediction))\n    #re

In [19]:
#plot predictions overlaid with observed:
plt.figure(figsize=(10,5),dpi=1200)
plt.style.use('dark_background')
#test data

x = np.arange(0,len(np.array(test_Y).flatten()))
plt.scatter(x,test_Y,s=4,c='r')

#prediction
x = np.arange(0,len(np.array(predictions).flatten()))
plt.title('LSTM Autoregressive Prediction')
plt.xlabel(f'Timepoint (Window Average, {smooth_out}hrs)')
plt.ylabel('Normalized Snow Depth')
plt.scatter(x,np.array(predictions).flatten(),s=.2,c='b',marker='+')

plt.show()

** Results ** 

-The LSTM fits very well to training data and validation data, with both losses approaching zero

-non-stately LSTM with shuffled dataset performs better on data validation

-Autoregression fails using this model. Explored with many hyperparameter permutations. 